In [46]:
import pandas as pd

In [47]:
df = pd.read_csv("nba_games.csv", index_col=0)

In [48]:
df

mp   mp.1    fg    fga    fg%    3p   3pa    3p%    ft   fta  ...  \
0      240.0  240.0  39.0   81.0  0.481   6.0  20.0  0.300  14.0  18.0  ...   
1      240.0  240.0  36.0  100.0  0.360   7.0  31.0  0.226  16.0  19.0  ...   
2      240.0  240.0  37.0   85.0  0.435   8.0  19.0  0.421  17.0  23.0  ...   
3      240.0  240.0  41.0   89.0  0.461   8.0  21.0  0.381  17.0  19.0  ...   
4      240.0  240.0  27.0   86.0  0.314   6.0  26.0  0.231  15.0  20.0  ...   
...      ...    ...   ...    ...    ...   ...   ...    ...   ...   ...  ...   
17767  240.0  240.0  35.0   81.0  0.432  11.0  26.0  0.423  27.0  36.0  ...   
17768  240.0  240.0  37.0   74.0  0.500  13.0  25.0  0.520  26.0  37.0  ...   
17769  240.0  240.0  42.0   89.0  0.472  14.0  33.0  0.424  10.0  20.0  ...   
17770  240.0  240.0  41.0   85.0  0.482   9.0  26.0  0.346  26.0  30.0  ...   
17771  240.0  240.0  33.0   85.0  0.388  12.0  44.0  0.273  28.0  34.0  ...   

       tov%_max_opp  usg%_max_opp  ortg_max_opp  drtg_max_opp  team_opp  \
0              22.8          29.0         178.0         111.0       DAL   
1              50.0          32.6         152.0         111.0       ATL   
2              20.0          30.9         148.0         116.0       SAS   
3              28.6          30.9         138.0         118.0       MIN   
4              16.8          30.9         157.0          90.0       MEM   
...             ...           ...           ...           ...       ...   
17767          34.2          33.7         160.0         118.0       OKC   
17768          25.0          30.0         139.0         129.0       ORL   
17769          25.6          29.9         175.0         126.0       LAC   
17770          27.7          27.1         150.0         126.0       MIA   
17771          51.5          36.2         141.0         114.0       BOS   

       total_opp  home_opp  season        date    won  
0             95         1    2016  2015-12-09   True  
1             98         0    2016  2015-12-09  False  
2            107         1    2018  2017-10-18  False  
3             99         0    2018  2017-10-18   True  
4             92         1    2021  2021-04-30  False  
...          ...       ...     ...         ...    ...  
17767         92         0    2019  2018-10-19   True  
17768        108         1    2017  2016-12-14   True  
17769        113         0    2017  2016-12-14  False  
17770        106         1    2020  2020-09-19   True  
17771        117         0    2020  2020-09-19  False  

[17772 rows x 150 columns]

In [49]:
df = df.sort_values("date")

In [50]:
df = df.reset_index(drop=True)

In [51]:
del df["mp.1"]
del df["mp_opp.1"]
del df["index_opp"]

In [52]:
def add_target(group):
    group["target"] = group["won"].shift(-1)
    return group

df = df.groupby("team", group_keys=False).apply(add_target).reset_index(drop=True)
df = df.copy()


/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/3664484873.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  group["target"] = group["won"].shift(-1)
/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/3664484873.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  group["target"] = group["won"].shift(-1)
/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/3664484873.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many tim

In [53]:
df["target"][pd.isnull(df["target"])] = 2
df["target"] = df["target"].astype(int, errors="ignore")

/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/2793819745.py:1: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df["target"][pd.isnull(df["target"])] = 2
/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/279381

In [54]:
df["won"].value_counts()

won
False    8886
True     8886
Name: count, dtype: int64

In [55]:
df["target"].value_counts()

target
1    8872
0    8870
2      30
Name: count, dtype: int64

In [56]:
nulls = pd.isnull(df).sum()

In [57]:
nulls = nulls[nulls > 0]

In [58]:
valid_columns = df.columns[~df.columns.isin(nulls.index)]

In [59]:
valid_columns

Index(['mp', 'fg', 'fga', 'fg%', '3p', '3pa', '3p%', 'ft', 'fta', 'ft%',
       ...
       'usg%_max_opp', 'ortg_max_opp', 'drtg_max_opp', 'team_opp', 'total_opp',
       'home_opp', 'season', 'date', 'won', 'target'],
      dtype='object', length=142)

In [60]:
df = df[valid_columns].copy()

In [61]:
df

mp    fg   fga    fg%    3p   3pa    3p%    ft   fta    ft%  ...  \
0      240.0  35.0  83.0  0.422   6.0  18.0  0.333  19.0  27.0  0.704  ...   
1      240.0  38.0  94.0  0.404   9.0  29.0  0.310  10.0  17.0  0.588  ...   
2      240.0  37.0  87.0  0.425   7.0  19.0  0.368  16.0  23.0  0.696  ...   
3      240.0  41.0  96.0  0.427   9.0  30.0  0.300  20.0  22.0  0.909  ...   
4      240.0  37.0  82.0  0.451   8.0  27.0  0.296  12.0  15.0  0.800  ...   
...      ...   ...   ...    ...   ...   ...    ...   ...   ...    ...  ...   
17767  240.0  34.0  85.0  0.400  15.0  38.0  0.395  14.0  19.0  0.737  ...   
17768  240.0  41.0  88.0  0.466   9.0  40.0  0.225  13.0  15.0  0.867  ...   
17769  240.0  31.0  75.0  0.413  11.0  32.0  0.344  21.0  31.0  0.677  ...   
17770  240.0  34.0  80.0  0.425  11.0  28.0  0.393  11.0  12.0  0.917  ...   
17771  240.0  38.0  92.0  0.413  19.0  46.0  0.413   8.0   8.0  1.000  ...   

       usg%_max_opp  ortg_max_opp  drtg_max_opp  team_opp  total_opp  \
0              43.7         206.0         104.0       GSW        111   
1              34.6         162.0         104.0       CHI         97   
2              29.0         138.0         105.0       CLE         95   
3              38.9         201.0         120.0       NOP         95   
4              23.6         132.0         104.0       DET        106   
...             ...           ...           ...       ...        ...   
17767          36.3         133.0         112.0       GSW        107   
17768          94.4         300.0         112.0       BOS         94   
17769          36.2         222.0         107.0       GSW        104   
17770          31.5         186.0         111.0       GSW        103   
17771          42.6         141.0         126.0       BOS         90   

       home_opp  season        date    won  target  
0             1    2016  2015-10-27  False       0  
1             1    2016  2015-10-27  False       1  
2             0    2016  2015-10-27   True       1  
3             0    2016  2015-10-27   True       1  
4             0    2016  2015-10-27  False       1  
...         ...     ...         ...    ...     ...  
17767         0    2022  2022-06-10  False       0  
17768         0    2022  2022-06-13   True       1  
17769         1    2022  2022-06-13  False       0  
17770         0    2022  2022-06-16  False       2  
17771         1    2022  2022-06-16   True       2  

[17772 rows x 142 columns]

In [62]:
from sklearn.linear_model import LogisticRegression
from sklearn.feature_selection import RFE
from sklearn.model_selection import TimeSeriesSplit, GridSearchCV
from sklearn.pipeline import Pipeline

logistic_model = LogisticRegression(max_iter=1000, verbose=True)

split = TimeSeriesSplit(n_splits=3)

search_space = {
    "classification__penalty": ["l1", "l2"],
    "classification__C": [0.1, 1, 10],
    "classification__solver": ["liblinear", "lbfgs"]
}

rfe = RFE(estimator=logistic_model, 
          n_features_to_select=30
         )

pipeline = Pipeline(steps=[('feature_selection', rfe), ('classification', logistic_model)])

gs = GridSearchCV(estimator=pipeline, param_grid=search_space, cv=split, scoring='accuracy')


In [63]:
removed_columns = ["season", "date", "won", "target", "team", "team_opp"]
selected_columns = df.columns[~df.columns.isin(removed_columns)]

In [64]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
df[selected_columns] = scaler.fit_transform(df[selected_columns])

In [65]:
df

mp        fg       fga       fg%        3p       3pa       3p%  \
0      0.0  0.363636  0.338235  0.366029  0.206897  0.212121  0.395487   
1      0.0  0.431818  0.500000  0.322967  0.310345  0.378788  0.368171   
2      0.0  0.409091  0.397059  0.373206  0.241379  0.227273  0.437055   
3      0.0  0.500000  0.529412  0.377990  0.310345  0.393939  0.356295   
4      0.0  0.409091  0.323529  0.435407  0.275862  0.348485  0.351544   
...    ...       ...       ...       ...       ...       ...       ...   
17767  0.0  0.340909  0.367647  0.313397  0.517241  0.515152  0.469121   
17768  0.0  0.500000  0.411765  0.471292  0.310345  0.545455  0.267221   
17769  0.0  0.272727  0.220588  0.344498  0.379310  0.424242  0.408551   
17770  0.0  0.340909  0.294118  0.373206  0.379310  0.363636  0.466746   
17771  0.0  0.431818  0.470588  0.344498  0.655172  0.636364  0.490499   

             ft       fta       ft%  ...  usg%_max_opp  ortg_max_opp  \
0      0.418605  0.412698  0.654609  ...      0.277279      0.554502   
1      0.209302  0.253968  0.519253  ...      0.160462      0.345972   
2      0.348837  0.349206  0.645274  ...      0.088575      0.232227   
3      0.441860  0.333333  0.893816  ...      0.215661      0.530806   
4      0.255814  0.222222  0.766628  ...      0.019255      0.203791   
...         ...       ...       ...  ...           ...           ...   
17767  0.302326  0.285714  0.693116  ...      0.182285      0.208531   
17768  0.279070  0.222222  0.844807  ...      0.928113      1.000000   
17769  0.465116  0.476190  0.623104  ...      0.181001      0.630332   
17770  0.232558  0.174603  0.903151  ...      0.120668      0.459716   
17771  0.162791  0.111111  1.000000  ...      0.263158      0.246445   

       drtg_max_opp  team_opp  total_opp  home_opp  season        date    won  \
0          0.317647       GSW   0.451923       1.0    2016  2015-10-27  False   
1          0.317647       CHI   0.317308       1.0    2016  2015-10-27  False   
2          0.329412       CLE   0.298077       0.0    2016  2015-10-27   True   
3          0.505882       NOP   0.298077       0.0    2016  2015-10-27   True   
4          0.317647       DET   0.403846       0.0    2016  2015-10-27  False   
...             ...       ...        ...       ...     ...         ...    ...   
17767      0.411765       GSW   0.413462       0.0    2022  2022-06-10  False   
17768      0.411765       BOS   0.288462       0.0    2022  2022-06-13   True   
17769      0.352941       GSW   0.384615       1.0    2022  2022-06-13  False   
17770      0.400000       GSW   0.375000       0.0    2022  2022-06-16  False   
17771      0.576471       BOS   0.250000       1.0    2022  2022-06-16   True   

       target  
0           0  
1           1  
2           1  
3           1  
4           1  
...       ...  
17767       0  
17768       1  
17769       0  
17770       2  
17771       2  

[17772 rows x 142 columns]

In [66]:
gs.fit(df[selected_columns], df["target"])

 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =          137     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.30490D-03

At iterate   50    f=  6.75812D-01    |proj g|=  3.08446D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
  137     69     81      1     0     0   8.180D-05   6.757D-01
  F =  0.67570383803667922     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =          136     M =           10

At X0         0 v

 This problem is unconstrained.
 This problem is unconstrained.



At iterate   50    f=  6.75812D-01    |proj g|=  3.08446D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
  135     69     81      1     0     0   8.180D-05   6.757D-01
  F =  0.67570383803513745     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =          134     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.30490D-03

At iterate   50    f=  6.75790D-01    |proj g|=  1.21561D-03

           * * *

Tit   = total number of iterations
Tnf   = total nu

 This problem is unconstrained.
 This problem is unconstrained.


...

 This problem is unconstrained.



At iterate   50    f=  6.96060D-01    |proj g|=  2.40537D-04

At iterate  100    f=  6.95976D-01    |proj g|=  3.74238D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   93    105    121      1     0     0   9.093D-05   6.960D-01
  F =  0.69597003006630687     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           93     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  1.09861D+00    |proj g|=  3.31645D-01


 This problem is unconstrained.



At iterate   50    f=  6.98419D-01    |proj g|=  3.31707D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   93     97    111      1     0     0   5.516D-05   6.981D-01
  F =  0.69809207625174929     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            


GridSearchCV(cv=TimeSeriesSplit(gap=0, max_train_size=None, n_splits=3, test_size=None),
             estimator=Pipeline(steps=[('feature_selection',
                                        RFE(estimator=LogisticRegression(max_iter=1000,
                                                                         verbose=True),
                                            n_features_to_select=30)),
                                       ('classification',
                                        LogisticRegression(max_iter=1000,
                                                           verbose=True))]),
             param_grid={'classification__C': [0.1, 1, 10],
                         'classification__penalty': ['l1', 'l2'],
                         'classification__solver': ['liblinear', 'lbfgs']},
             scoring='accuracy')

In [67]:
# Najlepszy model po GridSearchCV
best_model = gs.best_estimator_

# Wyświetlanie najlepszych parametrów
print("Najlepsze parametry: ", gs.best_params_)

best_rfe = best_model.named_steps['feature_selection']

Najlepsze parametry:  {'classification__C': 0.1, 'classification__penalty': 'l2', 'classification__solver': 'lbfgs'}


In [68]:
predictors = list(selected_columns[best_rfe.get_support()])

In [69]:
predictors

['fg',
 'fg%',
 '3pa',
 'ft%',
 'drb',
 'trb',
 'tov',
 '3par',
 'drb%',
 'trb%',
 'tov%',
 'drtg',
 'fga_max',
 '3p%_max',
 'ft%_max',
 'pf_max',
 '+/-_max',
 'drtg_max',
 'fg_opp',
 '3pa_opp',
 'ft_opp',
 'fta_opp',
 '3par_opp',
 'ftr_opp',
 'ortg_opp',
 '3p_max_opp',
 '3pa_max_opp',
 '3p%_max_opp',
 'ft%_max_opp',
 '3par_max_opp']

In [70]:
def backtest(data, model, predictors, start=2, step=1):
    all_predictions = []
    
    seasons = sorted(data["season"].unique())
    
    for i in range(start, len(seasons), step):
        season = seasons[i]
        train = data[data["season"] < season]
        test = data[data["season"] == season]
        
        model.fit(train[predictors], train["target"])
        
        preds = model.predict(test[predictors])
        preds = pd.Series(preds, index=test.index)
        combined = pd.concat([test["target"], preds], axis=1)
        combined.columns = ["actual", "prediction"]
        
        all_predictions.append(combined)
    return pd.concat(all_predictions)

In [71]:
predictions = backtest(df, best_model, predictors)

RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.36063D-03

At iterate   50    f=  6.85372D-01    |proj g|=  1.18442D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     53     65      1     0     0   7.642D-05   6.854D-01
  F =  0.68537028672594336     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 v

 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     42     49      1     0     0   7.172D-05   6.867D-01
  F =  0.68668075699136832     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.95078D-03

At iterate   50    f=  6.85330D-01    |proj g|=  1.30109D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments 

 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.50980D-03

At iterate   50    f=  6.85743D-01    |proj g|=  4.00919D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     87    103      1     0     0   9.128D-05   6.856D-01
  F =  0.68562539986310167     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 v

 This problem is unconstrained.
 This problem is unconstrained.



           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.58284D-03

At iterate   50    f=  6.86342D-01    |proj g|=  6.71085D-04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     62     78      1     0     0   8.953D-05   6.863D-01
  F =  0.68631048438643294     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at th

 This problem is unconstrained.


In [72]:
from sklearn.metrics import accuracy_score

accuracy_score(predictions["actual"], predictions["prediction"])

0.538252675291487

In [73]:
df

mp        fg       fga       fg%        3p       3pa       3p%  \
0      0.0  0.363636  0.338235  0.366029  0.206897  0.212121  0.395487   
1      0.0  0.431818  0.500000  0.322967  0.310345  0.378788  0.368171   
2      0.0  0.409091  0.397059  0.373206  0.241379  0.227273  0.437055   
3      0.0  0.500000  0.529412  0.377990  0.310345  0.393939  0.356295   
4      0.0  0.409091  0.323529  0.435407  0.275862  0.348485  0.351544   
...    ...       ...       ...       ...       ...       ...       ...   
17767  0.0  0.340909  0.367647  0.313397  0.517241  0.515152  0.469121   
17768  0.0  0.500000  0.411765  0.471292  0.310345  0.545455  0.267221   
17769  0.0  0.272727  0.220588  0.344498  0.379310  0.424242  0.408551   
17770  0.0  0.340909  0.294118  0.373206  0.379310  0.363636  0.466746   
17771  0.0  0.431818  0.470588  0.344498  0.655172  0.636364  0.490499   

             ft       fta       ft%  ...  usg%_max_opp  ortg_max_opp  \
0      0.418605  0.412698  0.654609  ...      0.277279      0.554502   
1      0.209302  0.253968  0.519253  ...      0.160462      0.345972   
2      0.348837  0.349206  0.645274  ...      0.088575      0.232227   
3      0.441860  0.333333  0.893816  ...      0.215661      0.530806   
4      0.255814  0.222222  0.766628  ...      0.019255      0.203791   
...         ...       ...       ...  ...           ...           ...   
17767  0.302326  0.285714  0.693116  ...      0.182285      0.208531   
17768  0.279070  0.222222  0.844807  ...      0.928113      1.000000   
17769  0.465116  0.476190  0.623104  ...      0.181001      0.630332   
17770  0.232558  0.174603  0.903151  ...      0.120668      0.459716   
17771  0.162791  0.111111  1.000000  ...      0.263158      0.246445   

       drtg_max_opp  team_opp  total_opp  home_opp  season        date    won  \
0          0.317647       GSW   0.451923       1.0    2016  2015-10-27  False   
1          0.317647       CHI   0.317308       1.0    2016  2015-10-27  False   
2          0.329412       CLE   0.298077       0.0    2016  2015-10-27   True   
3          0.505882       NOP   0.298077       0.0    2016  2015-10-27   True   
4          0.317647       DET   0.403846       0.0    2016  2015-10-27  False   
...             ...       ...        ...       ...     ...         ...    ...   
17767      0.411765       GSW   0.413462       0.0    2022  2022-06-10  False   
17768      0.411765       BOS   0.288462       0.0    2022  2022-06-13   True   
17769      0.352941       GSW   0.384615       1.0    2022  2022-06-13  False   
17770      0.400000       GSW   0.375000       0.0    2022  2022-06-16  False   
17771      0.576471       BOS   0.250000       1.0    2022  2022-06-16   True   

       target  
0           0  
1           1  
2           1  
3           1  
4           1  
...       ...  
17767       0  
17768       1  
17769       0  
17770       2  
17771       2  

[17772 rows x 142 columns]

In [74]:
df_rolling = df[list(selected_columns) + ["won", "team", "season"]]

def find_team_averages(team):
    numeric_cols = team.select_dtypes(include="number")
    rolling = numeric_cols.rolling(10).mean()
    
    rolling[["team", "season"]] = team[["team", "season"]]
    return rolling

df_rolling = df_rolling.groupby(["team", "season"], group_keys=False).apply(find_team_averages)


/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/410169298.py:10: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  df_rolling = df_rolling.groupby(["team", "season"], group_keys=False).apply(find_team_averages)


In [75]:
df_rolling

mp        fg       fga       fg%        3p       3pa       3p%  \
0      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
3      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
4      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...    ...       ...       ...       ...       ...       ...       ...   
17767  0.0  0.381818  0.292647  0.428230  0.468966  0.477273  0.448100   
17768  0.0  0.502273  0.364706  0.517703  0.455172  0.481818  0.440736   
17769  0.0  0.354545  0.279412  0.404545  0.437931  0.465152  0.429572   
17770  0.0  0.354545  0.294118  0.389952  0.434483  0.459091  0.431710   
17771  0.0  0.484091  0.379412  0.482297  0.486207  0.507576  0.448812   

             ft       fta       ft%  ...  stl%_max_opp  blk%_max_opp  \
0           NaN       NaN       NaN  ...           NaN           NaN   
1           NaN       NaN       NaN  ...           NaN           NaN   
2           NaN       NaN       NaN  ...           NaN           NaN   
3           NaN       NaN       NaN  ...           NaN           NaN   
4           NaN       NaN       NaN  ...           NaN           NaN   
...         ...       ...       ...  ...           ...           ...   
17767  0.434884  0.373016  0.764177  ...        0.0570        0.1113   
17768  0.320930  0.282540  0.757993  ...        0.0716        0.1171   
17769  0.434884  0.385714  0.736639  ...        0.0591        0.1113   
17770  0.406977  0.357143  0.754142  ...        0.0572        0.1111   
17771  0.316279  0.269841  0.801750  ...        0.0656        0.1152   

       tov%_max_opp  usg%_max_opp  ortg_max_opp  drtg_max_opp  total_opp  \
0               NaN           NaN           NaN           NaN        NaN   
1               NaN           NaN           NaN           NaN        NaN   
2               NaN           NaN           NaN           NaN        NaN   
3               NaN           NaN           NaN           NaN        NaN   
4               NaN           NaN           NaN           NaN        NaN   
...             ...           ...           ...           ...        ...   
17767      0.471908      0.170603      0.431754      0.522353   0.348077   
17768      0.374109      0.321566      0.642654      0.564706   0.392308   
17769      0.483229      0.174711      0.438863      0.483529   0.350000   
17770      0.483229      0.172144      0.460190      0.472941   0.344231   
17771      0.444025      0.308601      0.628910      0.568235   0.395192   

       home_opp  season  team  
0           NaN    2016   NOP  
1           NaN    2016   CLE  
2           NaN    2016   CHI  
3           NaN    2016   GSW  
4           NaN    2016   ATL  
...         ...     ...   ...  
17767       0.5    2022   BOS  
17768       0.4    2022   GSW  
17769       0.5    2022   BOS  
17770       0.5    2022   BOS  
17771       0.5    2022   GSW  

[17772 rows x 138 columns]

In [76]:
rolling_cols = [f"{col}_10" for col in df_rolling.columns]
df_rolling.columns = rolling_cols
df = pd.concat([df, df_rolling], axis=1)

In [77]:
df = df.dropna()

In [78]:
df

mp        fg       fga       fg%        3p       3pa       3p%  \
243    0.0  0.522727  0.382353  0.523923  0.344828  0.333333  0.457245   
251    0.0  0.659091  0.426471  0.645933  0.620690  0.515152  0.562945   
252    0.0  0.386364  0.382353  0.358852  0.206897  0.181818  0.445368   
253    0.0  0.500000  0.382353  0.497608  0.344828  0.318182  0.475059   
256    0.0  0.318182  0.132353  0.500000  0.275862  0.272727  0.432304   
...    ...       ...       ...       ...       ...       ...       ...   
17767  0.0  0.340909  0.367647  0.313397  0.517241  0.515152  0.469121   
17768  0.0  0.500000  0.411765  0.471292  0.310345  0.545455  0.267221   
17769  0.0  0.272727  0.220588  0.344498  0.379310  0.424242  0.408551   
17770  0.0  0.340909  0.294118  0.373206  0.379310  0.363636  0.466746   
17771  0.0  0.431818  0.470588  0.344498  0.655172  0.636364  0.490499   

             ft       fta       ft%  ...  stl%_max_opp_10  blk%_max_opp_10  \
243    0.255814  0.238095  0.708285  ...           0.0628           0.0679   
251    0.325581  0.238095  0.927655  ...           0.0613           0.0772   
252    0.511628  0.412698  0.827305  ...           0.0625           0.1145   
253    0.325581  0.349206  0.593932  ...           0.0646           0.0759   
256    0.581395  0.444444  0.879813  ...           0.0741           0.0982   
...         ...       ...       ...  ...              ...              ...   
17767  0.302326  0.285714  0.693116  ...           0.0570           0.1113   
17768  0.279070  0.222222  0.844807  ...           0.0716           0.1171   
17769  0.465116  0.476190  0.623104  ...           0.0591           0.1113   
17770  0.232558  0.174603  0.903151  ...           0.0572           0.1111   
17771  0.162791  0.111111  1.000000  ...           0.0656           0.1152   

       tov%_max_opp_10  usg%_max_opp_10  ortg_max_opp_10  drtg_max_opp_10  \
243           0.413522         0.124134         0.361611         0.449412   
251           0.469497         0.219641         0.394787         0.531765   
252           0.437841         0.138126         0.507109         0.360000   
253           0.512159         0.133633         0.277251         0.388235   
256           0.313312         0.179974         0.500000         0.471765   
...                ...              ...              ...              ...   
17767         0.471908         0.170603         0.431754         0.522353   
17768         0.374109         0.321566         0.642654         0.564706   
17769         0.483229         0.174711         0.438863         0.483529   
17770         0.483229         0.172144         0.460190         0.472941   
17771         0.444025         0.308601         0.628910         0.568235   

       total_opp_10  home_opp_10  season_10  team_10  
243        0.347115          0.4       2016      ATL  
251        0.324038          0.5       2016      GSW  
252        0.351923          0.6       2016      MEM  
253        0.308654          0.4       2016      IND  
256        0.380769          0.5       2016      POR  
...             ...          ...        ...      ...  
17767      0.348077          0.5       2022      BOS  
17768      0.392308          0.4       2022      GSW  
17769      0.350000          0.5       2022      BOS  
17770      0.344231          0.5       2022      BOS  
17771      0.395192          0.5       2022      GSW  

[15882 rows x 280 columns]

In [79]:
def shift_col(team, col_name):
    next_col = team[col_name].shift(-1)
    return next_col

def add_col(df, col_name):
    return df.groupby("team", group_keys=False).apply(lambda x: shift_col(x, col_name))

df["home_next"] = add_col(df, "home")
df["team_opp_next"] = add_col(df, "team_opp")
df["date_next"] = add_col(df, "date")

/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/1688004556.py:6: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  return df.groupby("team", group_keys=False).apply(lambda x: shift_col(x, col_name))
/var/folders/cf/2q1x6qbd7t10wbl_xmlrblfc0000gn/T/ipykernel_42005/1688004556.py:6: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  return df.groupby("team", group_keys=False).apply(lambda x: shift_col(

In [80]:
df

mp        fg       fga       fg%        3p       3pa       3p%  \
243    0.0  0.522727  0.382353  0.523923  0.344828  0.333333  0.457245   
251    0.0  0.659091  0.426471  0.645933  0.620690  0.515152  0.562945   
252    0.0  0.386364  0.382353  0.358852  0.206897  0.181818  0.445368   
253    0.0  0.500000  0.382353  0.497608  0.344828  0.318182  0.475059   
256    0.0  0.318182  0.132353  0.500000  0.275862  0.272727  0.432304   
...    ...       ...       ...       ...       ...       ...       ...   
17767  0.0  0.340909  0.367647  0.313397  0.517241  0.515152  0.469121   
17768  0.0  0.500000  0.411765  0.471292  0.310345  0.545455  0.267221   
17769  0.0  0.272727  0.220588  0.344498  0.379310  0.424242  0.408551   
17770  0.0  0.340909  0.294118  0.373206  0.379310  0.363636  0.466746   
17771  0.0  0.431818  0.470588  0.344498  0.655172  0.636364  0.490499   

             ft       fta       ft%  ...  usg%_max_opp_10  ortg_max_opp_10  \
243    0.255814  0.238095  0.708285  ...         0.124134         0.361611   
251    0.325581  0.238095  0.927655  ...         0.219641         0.394787   
252    0.511628  0.412698  0.827305  ...         0.138126         0.507109   
253    0.325581  0.349206  0.593932  ...         0.133633         0.277251   
256    0.581395  0.444444  0.879813  ...         0.179974         0.500000   
...         ...       ...       ...  ...              ...              ...   
17767  0.302326  0.285714  0.693116  ...         0.170603         0.431754   
17768  0.279070  0.222222  0.844807  ...         0.321566         0.642654   
17769  0.465116  0.476190  0.623104  ...         0.174711         0.438863   
17770  0.232558  0.174603  0.903151  ...         0.172144         0.460190   
17771  0.162791  0.111111  1.000000  ...         0.308601         0.628910   

       drtg_max_opp_10  total_opp_10  home_opp_10  season_10  team_10  \
243           0.449412      0.347115          0.4       2016      ATL   
251           0.531765      0.324038          0.5       2016      GSW   
252           0.360000      0.351923          0.6       2016      MEM   
253           0.388235      0.308654          0.4       2016      IND   
256           0.471765      0.380769          0.5       2016      POR   
...                ...           ...          ...        ...      ...   
17767         0.522353      0.348077          0.5       2022      BOS   
17768         0.564706      0.392308          0.4       2022      GSW   
17769         0.483529      0.350000          0.5       2022      BOS   
17770         0.472941      0.344231          0.5       2022      BOS   
17771         0.568235      0.395192          0.5       2022      GSW   

       home_next  team_opp_next   date_next  
243          0.0            BOS  2015-11-13  
251          1.0            BRK  2015-11-14  
252          0.0            MIN  2015-11-15  
253          0.0            CHI  2015-11-16  
256          0.0            CHO  2015-11-15  
...          ...            ...         ...  
17767        0.0            GSW  2022-06-13  
17768        0.0            BOS  2022-06-16  
17769        1.0            GSW  2022-06-16  
17770        NaN           None        None  
17771        NaN           None        None  

[15882 rows x 283 columns]

In [81]:
full = df.merge(df[rolling_cols + ["team_opp_next", "date_next", "team"]], left_on=["team", "date_next"], right_on=["team_opp_next", "date_next"])

In [82]:
full

mp        fg       fga       fg%        3p       3pa       3p%  \
0      0.00  0.477273  0.500000  0.375598  0.379310  0.348485  0.483373   
1      0.00  0.340909  0.250000  0.413876  0.310345  0.257576  0.509501   
2      0.50  0.409091  0.455882  0.330144  0.482759  0.515152  0.437055   
3      0.25  0.545455  0.544118  0.416268  0.413793  0.454545  0.419240   
4      0.00  0.340909  0.558824  0.186603  0.206897  0.469697  0.203088   
...     ...       ...       ...       ...       ...       ...       ...   
15769  0.00  0.545455  0.426471  0.511962  0.448276  0.469697  0.440618   
15770  0.00  0.477273  0.455882  0.409091  0.517241  0.590909  0.414489   
15771  0.00  0.340909  0.367647  0.313397  0.517241  0.515152  0.469121   
15772  0.00  0.500000  0.411765  0.471292  0.310345  0.545455  0.267221   
15773  0.00  0.272727  0.220588  0.344498  0.379310  0.424242  0.408551   

             ft       fta       ft%  ...  tov%_max_opp_10_y  \
0      0.441860  0.396825  0.730455  ...           0.380294   
1      0.511628  0.412698  0.827305  ...           0.437212   
2      0.372093  0.412698  0.568261  ...           0.504403   
3      0.186047  0.142857  0.883314  ...           0.467505   
4      0.139535  0.111111  0.854142  ...           0.413732   
...         ...       ...       ...  ...                ...   
15769  0.372093  0.365079  0.659277  ...           0.457128   
15770  0.255814  0.222222  0.766628  ...           0.471908   
15771  0.302326  0.285714  0.693116  ...           0.431761   
15772  0.279070  0.222222  0.844807  ...           0.483229   
15773  0.465116  0.476190  0.623104  ...           0.374109   

       usg%_max_opp_10_y  ortg_max_opp_10_y  drtg_max_opp_10_y  \
0               0.273427           0.270616           0.478824   
1               0.124904           0.404739           0.408235   
2               0.153273           0.344076           0.384706   
3               0.276508           0.352607           0.482353   
4               0.156739           0.470142           0.391765   
...                  ...                ...                ...   
15769           0.235173           0.562085           0.552941   
15770           0.170603           0.431754           0.522353   
15771           0.242875           0.567773           0.575294   
15772           0.174711           0.438863           0.483529   
15773           0.321566           0.642654           0.564706   

       total_opp_10_y  home_opp_10_y  season_10_y  team_10_y  team_opp_next_y  \
0            0.308654            0.6         2016        TOR              SAC   
1            0.428846            0.2         2016        SAC              TOR   
2            0.319231            0.7         2016        DET              CLE   
3            0.316346            0.7         2016        TOR              GSW   
4            0.436538            0.6         2016        NOP              DEN   
...               ...            ...          ...        ...              ...   
15769        0.429808            0.4         2022        GSW              BOS   
15770        0.348077            0.5         2022        BOS              GSW   
15771        0.394231            0.4         2022        GSW              BOS   
15772        0.350000            0.5         2022        BOS              GSW   
15773        0.392308            0.4         2022        GSW              BOS   

       team_y  
0         TOR  
1         SAC  
2         DET  
3         TOR  
4         NOP  
...       ...  
15769     GSW  
15770     BOS  
15771     GSW  
15772     BOS  
15773     GSW  

[15774 rows x 423 columns]

In [83]:
full[["team_x", "team_opp_next_x", "team_y", "team_opp_next_y", "date_next"]]

team_x team_opp_next_x team_y team_opp_next_y   date_next
0        SAC             TOR    TOR             SAC  2015-11-15
1        TOR             SAC    SAC             TOR  2015-11-15
2        CLE             DET    DET             CLE  2015-11-17
3        GSW             TOR    TOR             GSW  2015-11-17
4        DEN             NOP    NOP             DEN  2015-11-17
...      ...             ...    ...             ...         ...
15769    BOS             GSW    GSW             BOS  2022-06-10
15770    GSW             BOS    BOS             GSW  2022-06-13
15771    BOS             GSW    GSW             BOS  2022-06-13
15772    GSW             BOS    BOS             GSW  2022-06-16
15773    BOS             GSW    GSW             BOS  2022-06-16

[15774 rows x 5 columns]

In [84]:
removed_columns = list(full.columns[full.dtypes == "object"]) + removed_columns

In [85]:
removed_columns

['team_x',
 'team_opp',
 'date',
 'team_10_x',
 'team_opp_next_x',
 'date_next',
 'team_10_y',
 'team_opp_next_y',
 'team_y',
 'season',
 'date',
 'won',
 'target',
 'team',
 'team_opp']

In [86]:
selected_columns = full.columns[~full.columns.isin(removed_columns)]
rfe.fit(full[selected_columns], full["target"])

 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =          412     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  5.12806D-01

At iterate   50    f=  6.49378D-01    |proj g|=  1.35575D+00

At iterate  100    f=  6.29491D-01    |proj g|=  5.02976D-03

At iterate  150    f=  6.27629D-01    |proj g|=  4.62860D+00

At iterate  200    f=  6.27286D-01    |proj g|=  1.19663D+01

At iterate  250    f=  6.25881D-01    |proj g|=  7.87543D+00

At iterate  300    f=  6.25699D-01    |proj g|=  7.96317D-03

At iterate  350    f=  6.25693D-01    |proj g|=  9.82746D-02

At iterate  400    f=  6.25098D-01    |proj g|=  1.88284D-01

At iterate  450    f=  6.24650D-01    |proj g|=  3.12065D-01

At iterate  500    f=  6.24386D-01    |proj g|=  1.35771D-01

At iterate  550    f=  6.24384D-01    |proj g|=  2.10485D-02

At iterate  600    f=  6.23835D-01    |proj g|=  4.35323D-02

At iterate  650    f=  6.2

/Users/karol/Documents/studia/licencjat/nba ml/venv/lib/python3.12/site-packages/sklearn/linear_model/_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
 This problem is unconstrained.



At iterate 1000    f=  6.22521D-01    |proj g|=  3.20992D-02

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
  412   1000   1191      1     0     0   3.210D-02   6.225D-01
  F =  0.62252096647718347     

STOP: TOTAL NO. of ITERATIONS REACHED LIMIT                 
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =          411     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  5.12806D-01

At iterate   50    f=  6.49378D-01    |proj g|=  1.35575D+00

At iterate  100    f=  6.29491D-01    |proj g|=  5.02976D-03

At iter

/Users/karol/Documents/studia/licencjat/nba ml/venv/lib/python3.12/site-packages/sklearn/linear_model/_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
 This problem is unconstrained.


...

 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   38     21     24      1     0     0   7.643D-05   6.415D-01
  F =  0.64151096762124227     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           37     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.63514D-03

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates

 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     24     28      1     0     0   7.202D-05   6.423D-01
  F =  0.64232432817644280     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            


RFE(estimator=LogisticRegression(max_iter=1000, verbose=True),
    n_features_to_select=30)

In [87]:
predictors = list(selected_columns[rfe.get_support()])

In [88]:
predictors

['ast_10_x',
 'ortg_10_x',
 'drtg_10_x',
 'ft_max_10_x',
 'pts_max_10_x',
 '+/-_max_10_x',
 'usg%_max_10_x',
 '3p%_opp_10_x',
 'blk_opp_10_x',
 'pts_opp_10_x',
 'ortg_opp_10_x',
 'orb%_max_opp_10_x',
 'drtg_max_opp_10_x',
 'total_opp_10_x',
 'fg_10_y',
 '3pa_10_y',
 'ast_10_y',
 'drtg_10_y',
 'ft_max_10_y',
 'pts_max_10_y',
 '+/-_max_10_y',
 'trb%_max_10_y',
 '3p%_opp_10_y',
 'blk_opp_10_y',
 'pts_opp_10_y',
 'ortg_opp_10_y',
 'drtg_opp_10_y',
 'orb%_max_opp_10_y',
 'drtg_max_opp_10_y',
 'total_opp_10_y']

In [89]:
predictions = backtest(full, logistic_model, predictors)

RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.58494D-03

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     27     30      1     0     0   8.231D-05   6.431D-01
  F =  0.64307210164132911     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.9

 This problem is unconstrained.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   31     19     24      1     0     0   8.244D-05   6.396D-01
  F =  0.63963643809529835     

CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL            
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           31     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  6.93147D-01    |proj g|=  4.76653D-03

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates

 This problem is unconstrained.
 This problem is unconstrained.
 This problem is unconstrained.


In [90]:
wynik = accuracy_score(predictions["actual"], predictions["prediction"])
print(f"wynik to {wynik*100:.4f}"+"% dokładności osiągniętej przez Recursive Feature Elimination z najlepszym modelem.")

wynik to 63.1162% dokładności osiągniętej przez Recursive Feature Elimination z najlepszym modelem.
